作业16
如果某质量为m的天体，从无穷远处到被黑洞吸积到最小稳定轨道（3Rs），释放的能量是多少?

$R_s = \frac{2GM}{c^2}$

无穷远处的能量：$E=mc^2$

在圆轨道$3R_s$处的能量为：？




如果一个星系中的AGN光度超过恒星光度，其黑洞质量与恒星质量的比值最低是多少？

$L_E \sim 30000 \times \frac{M_\text{BH}}{M_{\odot}}L_{\odot}$

$L_* = \frac{M_*}3\times L_\odot$

假设$L_{AGN}\approx L_{Edd} > L_*$

$30000\times \frac{M_\text{BH}}{M_{\odot}}L_\odot > \dfrac{M_*}{3}L_\odot$

得到$\frac{M_\text{BH}}{M_*}>\dfrac{1}{90000}$

import numpy as np
import matplotlib.pyplot as plt
from astropy.cosmology import Planck18 as cosmo
from astropy.io import fits
from scipy.ndimage import zoom

# 假设我们有一个低红移星系的 FITS 图像
low_redshift_image_file = '149.74358_2.125144_sci.fits'
hdul = fits.open(low_redshift_image_file)
image_data = hdul[1].data
header = hdul[0].header
# 显示原始图像
plt.imshow(image_data, cmap='gray', origin='lower')
plt.colorbar(label='Flux')
plt.title('raw iamge')
plt.show()

def k_correction(z_old, z_new, wave_length_rest):
    """
    简单的 K-修正计算函数（假设一个粗略的模型）。
    
    参数:
    - z_old: 原始红移
    - z_new: 目标红移
    - wave_length_rest: 本征波长（单位：微米）
    
    返回:
    - k_corr: K-修正因子
    """
    # 简化的 K-修正：可以使用一个线性模型或经验公式
    delta_z = z_new - z_old
    k_corr = 2.5 * np.log10(1 + delta_z)  # 一个非常粗略的估计

    return k_corr

def apply_redshift_and_k_correction(image_data, z_old, z_new, wave_length_rest):
    """
    将星系从低红移 z_old 移动到更高红移 z_new，并应用红移效应和 K-修正。
    
    参数:
    - image_data: 原始星系图像数据 (2D numpy array)
    - z_old: 原始红移
    - z_new: 目标红移
    - wave_length_rest: 本征波长（单位：微米）
    
    返回:
    - new_image_data: 应用红移效应和 K-修正后的星系图像数据
    """
    # 计算表面亮度衰减因子
    surface_brightness_factor = (1 + z_old)**4 / (1 + z_new)**4

    # 计算 K-修正
    k_corr = k_correction(z_old, z_new, wave_length_rest)

    # 调整图像亮度，考虑表面亮度衰减和 K-修正
    new_image_data = image_data * surface_brightness_factor * 10**(-0.4 * k_corr)

    # 缩放空间分辨率
    scale_factor = (1 + z_old) / (1 + z_new)
    from scipy.ndimage import zoom
    new_image_data = zoom(new_image_data, scale_factor)

    return new_image_data

# 设置原始和目标红移
z_old = 0.05  # 低红移
z_new = 1.0   # 更高红移
wave_length_rest = 0.5  # 假设的本征波长（单位：微米）

# 应用红移效应和 K-修正
new_image_data = apply_redshift_and_k_correction(image_data, z_old, z_new, wave_length_rest)

# 显示应用红移效应和 K-修正后的星系图像
plt.imshow(new_image_data, cmap='gray', origin='lower')
plt.colorbar(label='Flux')
plt.title(f'new image')
plt.show()

task_18. 对于作业5或者作业15中的星系，采取至少一种方法来（定量）评估该星系所处的环境

要评估一个星系所处的环境，给定星系的坐标（赤经 RA、赤纬 DEC）和红移 ( z )，我们通常需要计算该星系在宇宙中的位置，并分析其周围其他星系的分布密度。这里我们可以通过以下步骤来评估该星系所处的环境：

1. 通过红移估算星系的距离
通过红移 ( z )，我们可以计算星系的距离。最简单的距离计算方法是基于“哈勃定律”或者使用一个宇宙学模型。哈勃定律公式为： [ D = \frac{c \times z}{H_0} ] 其中：

( D ) 是星系的距离，单位为 Mpc（百万秒差距）。
( c ) 是光速，约为 300,000 km/s。
( z ) 是红移。
( H_0 ) 是哈勃常数，常用值为 ( H_0 = 70 , \text{km/s/Mpc} )。
2. 将星系坐标从天球坐标转换为空间坐标
使用星系的赤经和赤纬坐标，我们可以将它们转换为三维空间坐标。结合估算的距离（通过红移），我们可以得到星系的三维空间位置。

3. 计算局部密度
为了评估星系的环境，可以通过计算它周围一定半径内的邻近星系的数量（或质量密度）来进行局部密度估算。这些星系的分布可以帮助我们了解目标星系所在的密集或稀疏区域。

代码实现
假设你有目标星系的坐标（赤经 RA，赤纬 DEC）和红移 ( z )，我们可以按照以下步骤来实现这一过程：

1. 计算星系距离
首先，计算星系的距离。我们可以使用简单的哈勃定律来进行距离估算。

import numpy as np

# 计算距离的函数
def calculate_distance(z, H0=70, c=300000):
    # 计算哈勃定律距离（单位：Mpc）
    return (c * z) / H0

# 目标星系的红移
z = 0.03  # 假设红移为 0.03

# 计算距离
distance = calculate_distance(z)
print(f"目标星系的距离为 {distance:.2f} Mpc")
2. 将天球坐标转换为三维空间坐标
假设星系的坐标是赤经 RA 和赤纬 DEC，我们需要将其转换为三维空间坐标。

# 将天球坐标 (RA, DEC) 转换为笛卡尔坐标 (x, y, z)
def sky_to_cartesian(ra, dec, z):
    # 计算星系的距离
    distance = calculate_distance(z)

    # 将角度转换为弧度
    ra_rad = np.radians(ra)
    dec_rad = np.radians(dec)

    # 计算笛卡尔坐标
    x = distance * np.cos(dec_rad) * np.cos(ra_rad)
    y = distance * np.cos(dec_rad) * np.sin(ra_rad)
    z = distance * np.sin(dec_rad)

    return np.array([x, y, z])

# 目标星系的坐标
ra = 150  # 假设赤经 RA 为 150 度
dec = 2.5  # 假设赤纬 DEC 为 2.5 度

# 转换为三维坐标
position = sky_to_cartesian(ra, dec, z)
print(f"目标星系的三维空间坐标为 {position}")
3. 计算局部密度
为了评估星系的环境，我们需要知道周围的星系分布。通常可以通过以下方式来评估局部密度：

使用附近的邻近星系数目：在给定半径范围内计算邻近星系的数目。这个方法通常使用一个球形半径（例如 1 Mpc）来计算星系的局部密度。
我们可以通过给定半径范围，计算目标星系附近的其他星系数量。

from scipy.spatial import KDTree

# 假设我们有多个星系的三维空间坐标
# 这里使用假数据作为示例
ra_list = [150, 151, 152, 160, 170]  # 假设的星系赤经
dec_list = [2.5, 3.0, 2.8, 1.5, 2.6]  # 假设的星系赤纬
z_list = [0.03, 0.04, 0.05, 0.02, 0.03]  # 假设的星系红移

# 计算所有星系的三维坐标
positions = np.array([sky_to_cartesian(ra, dec, z) for ra, dec, z in zip(ra_list, dec_list, z_list)])

# 使用 KDTree 计算星系的最近邻
tree = KDTree(positions)

# 目标星系的索引
target_index = 0

# 查询目标星系周围 1 Mpc 半径内的 10 个最近邻星系
distances, indices = tree.query(positions[target_index], k=10)

# 计算在 1 Mpc 内的星系数量
radius = 1.0  # 半径为 1 Mpc
neighbors_within_radius = sum(distances < radius)
print(f"目标星系周围 {radius} Mpc 内的星系数量：{neighbors_within_radius}")
评估环境：
如果目标星系周围的星系数量很高，表明该星系位于一个密集的区域，可能是星系团的一部分。
如果星系数量较少，说明目标星系可能位于一个较为稀疏的区域。
小结：
通过上述步骤，我们可以：

计算星系的距离，从而将其位置映射到三维空间中。
评估星系周围的密度，通过查询邻近星系的分布来定量评估星系所处的环境。